# Purpose

After 5 years of not having a satisfactory line plot animation approach in a jupyter notebook, figure out how to do it with matplotlib so that is is smooth and fast.

# Information

See `Interactive JS widgets for animation` section at [New in Matplotlib 2.1.0](https://matplotlib.org/3.3.3/users/prev_whats_new/whats_new_2.1.0.html) which recommends using the following

    from IPython.display import HTML
    HTML(animation.to_jshtml())
    
as opposed to setting `plt.rcParams["animation.html"] = "jshtml"`, which could alternatively be used. In either case, what is happening is the animation data is computed for all time steps (frames) and then all of the frames are sent to the frontend where javascript code successively presents each frame. For this reason it can take a little while to do the calculation of all of the frames.

See [matplotlib.animation.FuncAnimation](https://matplotlib.org/api/_as_gen/matplotlib.animation.FuncAnimation.html#matplotlib.animation.FuncAnimation) for function signature and arguments. Pay particular attention to `frames`, `save_count`, and `interval`.


# Approach

Animate propagating sine and cosine waves of the form $cos(\omega t - k z)$ and $sin(\omega t - k z)$. Select time interval and duration so that it loops after one period has propagated so it looks like a smoothly propagating wave.

$$
\omega = 2\pi f \\
f = \text{Frequency (Hz)} \\
k = 2 \pi / \lambda \\
\lambda = v / f = \text{wavelength (m)} \\
v = \text{velocity (m/s)}
$$

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
%matplotlib notebook
from IPython.display import HTML

freq_Hz = 1e8
velocity_mps = 2e8
wavelength_m = velocity_mps / freq_Hz
period_s = 1. / freq_Hz

print(f" Frequency: {freq_Hz:,} (Hz)")
print(f"  Velocity: {velocity_mps:,} (m/s)")
print(f"Wavelength: {wavelength_m:,} (m)")
print(f"    Period: {period_s} (s)")

omega = 2 * np.pi * freq_Hz
k = 2 * np.pi / wavelength_m

z_max = 2 * wavelength_m
numpnts_z = 201
z = np.linspace(0, z_max, numpnts_z)

t_max = period_s
numpnts_t = 100
t = np.linspace(0, t_max, numpnts_t, endpoint=False)

def trig_argument(t_i):
    """Trig argument for time t_i over array of positions z.
    """
    return omega * t_i - k * z

fig, ax = plt.subplots()
ax.set_xlabel('Distance (m)')
ax.set_ylabel('Amplitude')
ax.set_xlim(0, z_max)
ax.grid()

arg = trig_argument(t[0])
line1, = ax.plot(z, np.cos(arg))
line2, = ax.plot(z, np.sin(arg))

def animate(i):
    arg = trig_argument(t[i])
    line1.set_ydata(np.cos(arg))  # update line1 data.
    line2.set_ydata(np.sin(arg))  # update line2 data.
    return [line1, line2]

ani = animation.FuncAnimation(
    fig, animate, interval=20, blit=True, save_count=numpnts_t)

HTML(ani.to_jshtml())

 Frequency: 100,000,000.0 (Hz)
  Velocity: 200,000,000.0 (m/s)
Wavelength: 2.0 (m)
    Period: 1e-08 (s)


<IPython.core.display.Javascript object>